<a href="https://colab.research.google.com/github/narayananv10/NLP/blob/master/M2_J054_NLP.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np 
import pandas as pd
from bs4 import BeautifulSoup
import nltk
import pickle
import random
nltk.download('stopwords')
from nltk.corpus import stopwords
german_stop_words = stopwords.words('german')
from nltk.tokenize import WordPunctTokenizer
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))


! wget https://github.com/amsurve/J050_sem6_nlp/blob/master/datasets/10k-german-news-articles.zip?raw=true
! mkdir newsarticles
! unzip 10k-german-news-articles.zip?raw=true -d newsarticles
posts_df=pd.read_csv("/content/newsarticles/Posts.csv")
df = pd.read_csv('/content/newsarticles/Articles.csv')
df1 = df[:1000]

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
--2020-03-03 18:03:58--  https://github.com/amsurve/J050_sem6_nlp/blob/master/datasets/10k-german-news-articles.zip?raw=true
Resolving github.com (github.com)... 192.30.253.112
Connecting to github.com (github.com)|192.30.253.112|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://github.com/amsurve/J050_sem6_nlp/raw/master/datasets/10k-german-news-articles.zip [following]
--2020-03-03 18:03:58--  https://github.com/amsurve/J050_sem6_nlp/raw/master/datasets/10k-german-news-articles.zip
Reusing existing connection to github.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://media.githubusercontent.com/media/amsurve/J050_sem6_nlp/master/datasets/10k-german-news-articles.zip [following]
--2020-03-03 18:03:58--  https://media.githubusercontent.com/media/amsurve/J050_sem6_nlp/master/datasets/10k-german-news-articles.zip
R

# Preprocessing


In [0]:
def htmltagremover(sent):
    sent = BeautifulSoup(sent)
    for s in sent(["script", "style"]):
        s.extract() 
    text = sent.get_text()
    lines = (line.strip() for line in text.splitlines())
    chunks = (phrase.strip() for line in lines for phrase in line.split("  "))
    text = '\n'.join(chunk for chunk in chunks if chunk)
    return text

In [0]:
def remove_stopwords(text):
    token = text.split()
    return ' '.join([w for w in token if not w in german_stop_words])

In [0]:
def remove_punctuation(text):
    text = [i for i in text if i.isalnum() or i.isalpha() or i.isspace()]
    return ''.join(text)

In [0]:
def shortwords(text):
    text = ' '.join([w for w in text.split() if len(w)>3])
    return text

In [0]:
def tokenize(s):
    return nltk.tokenize.WordPunctTokenizer().tokenize(s)

In [0]:
def preprocess(s):
    text = htmltagremover(s)
    text = remove_stopwords(text)
    text = shortwords(text)
    text = remove_punctuation(text)
    text = tokenize(text)
    return text

# Body Topic Modelling

In [0]:
df1.Body = df1.Body.apply(preprocess)
final_data = df1.Body

/usr/local/lib/python3.6/dist-packages/pandas/core/generic.py:5208: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value


In [0]:
corpus_dict = corpora.Dictionary(final_data)
corpus = [corpus_dict.doc2bow(text) for text in final_data]
print(corpus)

[[(0, 1), (1, 1), (2, 2), (3, 1), (4, 1), (5, 1), (6, 2), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 2), (24, 1), (25, 2), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 3), (50, 1), (51, 1), (52, 1), (53, 3), (54, 1), (55, 2), (56, 1), (57, 2), (58, 1), (59, 4), (60, 1), (61, 1), (62, 1), (63, 1), (64, 1), (65, 1), (66, 1), (67, 1), (68, 2), (69, 1), (70, 1), (71, 1), (72, 1), (73, 1), (74, 1), (75, 1), (76, 1), (77, 2), (78, 1), (79, 1), (80, 1), (81, 2), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 1), (91, 1), (92, 1), (93, 1), (94, 3), (95, 1), (96, 1), (97, 2), (98, 1), (99, 1), (100, 1), (101, 1), (102, 1), (103, 3), (104, 1), (105, 1), (106, 1), (107, 1), (108, 1), (109, 1), (110, 1)

In [0]:
bodyTM = gensim.models.ldamodel.LdaModel(corpus=corpus,id2word=corpus_dict,num_topics=5,passes=10,alpha='auto',per_word_topics=5)

In [0]:
bodyTM.print_topics()

[(0,
  '0.004*"mehr" + 0.003*"Prozent" + 0.003*"ist" + 0.003*"werden" + 0.002*"wurde" + 0.002*"Österreich" + 0.002*"Menschen" + 0.002*"zwei" + 0.002*"schon" + 0.002*"Euro"'),
 (1,
  '0.003*"wurde" + 0.003*"ist" + 0.002*"mehr" + 0.002*"werden" + 0.002*"sagte" + 0.002*"zwei" + 0.002*"bereits" + 0.002*"Wien" + 0.002*"schon" + 0.001*"sagt"'),
 (2,
  '0.003*"werden" + 0.003*"mehr" + 0.003*"wurde" + 0.002*"Prozent" + 0.002*"gibt" + 0.002*"schon" + 0.002*"Euro" + 0.002*"ist" + 0.002*"Österreich" + 0.002*"sagte"'),
 (3,
  '0.004*"Prozent" + 0.003*"mehr" + 0.002*"wurde" + 0.002*"schon" + 0.002*"Österreich" + 0.002*"werden" + 0.002*"ist" + 0.001*"zwei" + 0.001*"sagte" + 0.001*"haben"'),
 (4,
  '0.004*"mehr" + 0.003*"wurde" + 0.003*"werden" + 0.002*"Euro" + 0.002*"Jahr" + 0.002*"Millionen" + 0.002*"worden" + 0.002*"wurden" + 0.002*"Prozent" + 0.002*"ist"')]

# Title Topic Modelling

In [0]:
 df1.Title = df1.Title.apply(preprocess)
 final_data1 = df1.Title

/usr/local/lib/python3.6/dist-packages/pandas/core/generic.py:5208: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value


In [0]:
corpus_dict_title = corpora.Dictionary(final_data1)
corpus_title = [corpus_dict_title.doc2bow(text) for text in final_data1]
print(corpus)

[[(0, 1), (1, 1), (2, 2), (3, 1), (4, 1), (5, 1), (6, 2), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1), (23, 2), (24, 1), (25, 2), (26, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 3), (50, 1), (51, 1), (52, 1), (53, 3), (54, 1), (55, 2), (56, 1), (57, 2), (58, 1), (59, 4), (60, 1), (61, 1), (62, 1), (63, 1), (64, 1), (65, 1), (66, 1), (67, 1), (68, 2), (69, 1), (70, 1), (71, 1), (72, 1), (73, 1), (74, 1), (75, 1), (76, 1), (77, 2), (78, 1), (79, 1), (80, 1), (81, 2), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 1), (91, 1), (92, 1), (93, 1), (94, 3), (95, 1), (96, 1), (97, 2), (98, 1), (99, 1), (100, 1), (101, 1), (102, 1), (103, 3), (104, 1), (105, 1), (106, 1), (107, 1), (108, 1), (109, 1), (110, 1)

In [0]:
titleTM = gensim.models.ldamodel.LdaModel(corpus=corpus_title,id2word=corpus_dict_title,num_topics=5,passes=10,alpha='auto',per_word_topics=5)

In [0]:
titleTM.print_topics()

[(0,
  '0.005*"Neue" + 0.003*"Obama" + 0.003*"Die" + 0.003*"macht" + 0.003*"Apple" + 0.003*"Eine" + 0.002*"Einigung" + 0.002*"bleibt" + 0.002*"Gefahr" + 0.002*"Flüchtlinge"'),
 (1,
  '0.005*"Wiener" + 0.003*"gibt" + 0.003*"zwei" + 0.003*"Österreich" + 0.003*"Google" + 0.003*"gestorben" + 0.003*"geht" + 0.003*"Nach" + 0.003*"RotBlau" + 0.003*"Android"'),
 (2,
  '0.005*"Wien" + 0.003*"Wiener" + 0.003*"Österreich" + 0.003*"Deutscher" + 0.003*"warnt" + 0.002*"Steuerreform" + 0.002*"mehr" + 0.002*"Österreichs" + 0.002*"Warum" + 0.002*"Dollar"'),
 (3,
  '0.004*"neue" + 0.004*"Österreich" + 0.003*"neuer" + 0.003*"Euro" + 0.003*"Griechenland" + 0.003*"derStandardat" + 0.003*"Faymann" + 0.002*"Wien" + 0.002*"Apple" + 0.002*"immer"'),
 (4,
  '0.005*"mehr" + 0.005*"wechselt" + 0.003*"zurück" + 0.003*"Apple" + 0.003*"Jahre" + 0.003*"vier" + 0.003*"geht" + 0.003*"Zukunft" + 0.003*"Handy" + 0.002*"Zwei"')]

# PyLDAvis

In [0]:
!pip install pyldavis

     |████████████████████████████████| 1.6MB 20.3MB/s 
     |████████████████████████████████| 552kB 61.4MB/s 
  Created wheel for pyldavis: filename=pyLDAvis-2.1.2-py2.py3-none-any.whl size=97711 sha256=3f712b55595a9dff95b6f4422215e0565a12d055cc0d52b1dd3025c7f4a1c5f8
  Stored in directory: /root/.cache/pip/wheels/98/71/24/513a99e58bb6b8465bae4d2d5e9dba8f0bef8179e3051ac414
  Created wheel for funcy: filename=funcy-1.14-py2.py3-none-any.whl size=32042 sha256=e9b30441a9c02115c1524059b67f24676cbcf5d0f574460350508291bee5fd1a
  Stored in directory: /root/.cache/pip/wheels/20/5a/d8/1d875df03deae6f178dfdf70238cca33f948ef8a6f5209f2eb
Successfully built pyldavis funcy


In [0]:
body = []
for f in df1.Body:
    if random.random() > .99:
        print(f)
        body.append(f)

['Kommunikative', 'Klammer', 'bleibt', 'dabei', 'RauchTal', 'KeyViualWienHamburg', 'Rauch', 'Fruchtsäfte', 'GmbH', 'verpflichtet', 'deutsche', 'Kommunikationsagentur', 'Kolle', 'Rebbe', 'neue', 'Leadagentur', 'Hamburger', 'strategische', 'kreative', 'Weiterentwicklung', 'sowohl', 'Dachmarkeals', 'Submarken', 'begleiten', 'Kommunikative', 'Klammer', 'bleibt', 'dabei', 'RauchTal', 'KeyViual', 'Heimat', 'RauchBaumes', 'Schwerpunkte', 'Mediaplan', 'bleiben', 'vorerst', 'OoH', 'Print', 'Film', 'Eine', 'Ausweitung', 'neue', 'Kanäle', 'bereits', 'geplant', 'Mediaagentur', 'bleibt', 'Global', 'verantwortlich', 'red', '162015', 'foto', 'rauchkolle', 'rebbe', 'CreditsBei', 'Rauch', 'Geschäftsleiter', 'Marketing', 'Vertrieb', 'Daniel', 'Wüstner', 'Head', 'International', 'Marketing', 'Erich', 'Teufel', 'Kolle', 'Rebbe', 'Kreation', 'Stefan', 'Wübbe', 'Strategie', 'Ralph', 'Poser', 'Beratung', 'Andreas', 'WinterBuerke', 'Executive', 'Rolf', 'Leger', 'Art', 'Tobias', 'Fritschen', 'Text', 'David', '

In [0]:
dict_body = corpora.Dictionary(body)
corpus_body = [dict_body.doc2bow(text) for text in body]
pickle.dump(corpus_body, open('corpus.pkl', 'wb'))
dict_body.save('dictionary_bodyTM.gensim')

/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:402: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL


In [0]:
corpus_body1 = gensim.models.ldamodel.LdaModel(corpus_body, num_topics = 5, id2word=dict_body, passes=15)
corpus_body1.save('model_ldavis_body')
topics = bodyTM.print_topics(num_words=4)
for t in topics:
    print(t)

(0, '0.004*"mehr" + 0.003*"Prozent" + 0.003*"ist" + 0.003*"werden"')
(1, '0.003*"wurde" + 0.003*"ist" + 0.002*"mehr" + 0.002*"werden"')
(2, '0.003*"werden" + 0.003*"mehr" + 0.003*"wurde" + 0.002*"Prozent"')
(3, '0.004*"Prozent" + 0.003*"mehr" + 0.002*"wurde" + 0.002*"schon"')
(4, '0.004*"mehr" + 0.003*"wurde" + 0.003*"werden" + 0.002*"Euro"')


/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:402: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL


In [0]:
dictionary = gensim.corpora.Dictionary.load('dictionary_bodyTM.gensim')
corpus_body2 = pickle.load(open('corpus.pkl', 'rb'))
lda = gensim.models.ldamodel.LdaModel.load('model_ldavis_body')
import pyLDAvis.gensim
lda_display = pyLDAvis.gensim.prepare(lda, corpus_body1, dictionary, sort_topics=False)
pyLDAvis.display(lda_display)

/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:402: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL
/usr/local/lib/python3.6/dist-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [0]:
title = []
for f in df1.Title:
    if random.random() > .99:
        print(f)
        title.append(f)

['Urzeitlicher', 'Vogelzwerg', 'spektakulären', 'Schwanzfedern']
['Large', 'Hadron', 'Collider', 'läuft', 'drei', 'Jahre', 'durchgehend']
['Neue', 'Kämpfe', 'Ostukraine', 'Tschechows', 'Gewehr']
['Luxemburger', 'Ausländerwahlrecht']
['Österreich', 'hinkt', 'Internetgeschwindigkeit']
['KostenNutzenRechnung']
['Putins', 'wichtigster', 'Feind', 'Westen']
['Mann', 'Südafrika', 'PenisTransplantation', 'Vater']
['Steirischer', 'Landtag', 'Erste', 'Sitzung', 'Voves']
['Steuerreform', 'bringt', 'Gemeinden', 'lange', 'Dürre']
['Amazon', 'stellt', 'neuen', 'Kindle', 'Paperwhite', 'schärferem', 'Display']
['Deutscher', 'Bundestag', 'darf', 'NSASpählisten', 'direkt', 'sehen']


In [0]:
dict_title = corpora.Dictionary(title)
corpus_title = [dict_title.doc2bow(text) for text in title]
pickle.dump(corpus_title, open('corpus.pkl', 'wb'))
dict_title.save('dictionary_titleTM.gensim')

/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:402: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL


In [0]:
import gensim
corpus_title1 = gensim.models.ldamodel.LdaModel(corpus_title, num_topics = 5, id2word=dict_title, passes=15)
corpus_title1.save('model_ldavis_title')
topics_title = titleTM.print_topics(num_words=4)
for t in topics_title:
    print(t)

(0, '0.005*"Neue" + 0.003*"Obama" + 0.003*"Die" + 0.003*"macht"')
(1, '0.005*"Wiener" + 0.003*"zwei" + 0.003*"gibt" + 0.003*"Österreich"')
(2, '0.005*"Wien" + 0.003*"Wiener" + 0.003*"Österreich" + 0.003*"Deutscher"')
(3, '0.004*"neue" + 0.004*"Österreich" + 0.003*"neuer" + 0.003*"Euro"')
(4, '0.005*"mehr" + 0.005*"wechselt" + 0.003*"zurück" + 0.003*"Apple"')


/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for

In [0]:
dictionary_title1 = gensim.corpora.Dictionary.load('dictionary_titleTM.gensim')
corpus_title2 = pickle.load(open('corpus.pkl', 'rb'))
ldatitle = gensim.models.ldamodel.LdaModel.load('model_ldavis_title')
import pyLDAvis.gensim
lda_displayt = pyLDAvis.gensim.prepare(ldatitle, corpus_title2, dictionary_title1, sort_topics=False)
pyLDAvis.display(lda_displayt)

/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:402: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL
/usr/local/lib/python3.6/dist-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))
